In [1]:
import numpy as np
import bokeh
from bokeh.plotting import show
import matplotlib.pyplot as plt
import flowkit as fk
import os
import pandas as pd
#import convexgating

In [2]:


bokeh.io.output_notebook()
%matplotlib inline

_ = plt.ioff()

Loading BokehJS ...

## ConvexGating strategy as flowkit strategy

### Functions

In [7]:
def make_gate_edges_object_string(cluster,hierarchy):
    return 'cluster_' + cluster + '_gate_edges_hierarchy_' + str(hierarchy) + '.csv'

def get_flowkit_gating_strategy(base_path,cluster):
    #base_path: location of ConvexGating output files
    #cluster: cluster identifier in ConvexGating run

    # initialize flowkit gating strategy
    #key_cl = next((key for key, value in cg_meta_info['clusterkeys'].items() if value == cluster), None)
    #print(key_cl)
    g_strat = fk.GatingStrategy()

    # get gating depth
    perf_summary_df = pd.read_csv(os.path.join(base_path,'performance_summary.csv'))
    marker_csv = pd.read_csv(os.path.join(base_path,'marker_summary.csv'))
    perf_summary_df['cluster'] = perf_summary_df['cluster'].astype(str)
    max_hierarchy = perf_summary_df[(perf_summary_df['cluster'] == str(cluster))]['hierarchy'].values[0] 

    #loop over hierarchies
    for hierarchy in range(1,max_hierarchy+1):
        hierarchy_string = os.path.join(base_path,'cluster_' + cluster,make_gate_edges_object_string(cluster,hierarchy))
        vertices_hierarchy = pd.read_csv(hierarchy_string,index_col=0)
        vertices = list(zip(vertices_hierarchy['x_coordinate'], vertices_hierarchy['y_coordinate']))
        try:
            markers = list(marker_csv[(marker_csv['cluster'] == int(cluster)) & ((marker_csv['hierarchy'] == hierarchy))]['marker'])
            if len(markers) == 0:
                markers = list(marker_csv[(marker_csv['cluster'] == cluster) & ((marker_csv['hierarchy'] == hierarchy))]['marker'])
        except:
            markers = list(marker_csv[(marker_csv['cluster'] == cluster) & ((marker_csv['hierarchy'] == hierarchy))]['marker'])
        dim_a = fk.Dimension(markers[0])
        dim_b = fk.Dimension(markers[1])
        poly_gate = fk.gates.PolygonGate('hierarchy_' + str(hierarchy),dimensions= [dim_a,dim_b],vertices=vertices)
        if hierarchy == 1:
            gate_path_tuple = ('root',)
        else:
            gate_path_tuple = tuple(['root'] + ['hierarchy_' + str(i) for i in range(1, hierarchy)])
        g_strat.add_gate(poly_gate, gate_path = gate_path_tuple) 
    return g_strat

def add_flowkit_gating_strategies(base_path):
    meta_info_path = os.path.join(base_path,"meta_info.npy")
    flowkit_path = os.path.join(base_path,'flowkit_export')
    if not os.path.exists(flowkit_path):
        os.mkdir(flowkit_path)
    meta_info = np.load(meta_info_path,allow_pickle='TRUE').item()
    flowkit_strategies_dict = {}
    for cluster in list(meta_info['clusterkeys'].values()):
        flowkit_strategies_dict[cluster] = get_flowkit_gating_strategy(base_path,cluster)
    np.save(os.path.join(flowkit_path, "flowkit_strategies.npy"), flowkit_strategies_dict)

def export_strategies(base_path):
    flowkit_path = os.path.join(base_path,'flowkit_export')
    flowkit_fcs_path = os.path.join(flowkit_path,'fcs_samples')
    flowkit_wsp_path = os.path.join(flowkit_path,'wsp_files')
    meta_info_path = os.path.join(base_path,"meta_info.npy")
    meta_info = np.load(meta_info_path,allow_pickle='TRUE').item()
    flowkit_fcs_path = os.path.join(flowkit_path,'fcs_samples')
    flowkit_wsp_path = os.path.join(flowkit_path,'wsp_files')
    if not os.path.exists(flowkit_fcs_path):
            os.mkdir(flowkit_fcs_path)
    if not os.path.exists(flowkit_wsp_path):
            os.mkdir(flowkit_wsp_path)
    flowkit_strategies = np.load(os.path.join(flowkit_path, "flowkit_strategies.npy"),allow_pickle = True).item()
    for key in meta_info['clusterkeys'].keys():
        cluster = meta_info['clusterkeys'][key]
        sample_data = meta_info['general_summary'][key].filter(regex=r'^(?!gate_|new_gate_|final_gate_|true_label)')
        sample_label = meta_info['general_summary'][key][['true_label']]
        sample = fk.Sample(sample_data,sample_id = str(cluster))
        flowkit_out = flowkit_strategies[cluster].gate_sample(sample)
        sample.export(os.path.join(flowkit_fcs_path, 'fcs_cluster_' + cluster + '.fcs'),source='raw')
        fk._utils.wsp_utils.export_flowjo_wsp(flowkit_strategies[cluster],
                                              'wsp_cluster_' + str(cluster),
                                              [sample],
                                              os.path.join(flowkit_wsp_path,'wsp_cluster_' + str(cluster) + '.wsp'))

### Apply

In [8]:
base_path = os.path.join("C:\\Users","vfriedrich","projects","gating","tests","add_hull_try_out","GL01_oetjen_strategies")
add_flowkit_gating_strategies(base_path)
export_strategies(base_path)

### Visualize

In [ ]:


meta_info_path = os.path.join(base_path,"meta_info.npy")
meta_info = np.load(meta_info_path,allow_pickle='TRUE').item()
flowkit_path = os.path.join(base_path,'flowkit_export')
flowkit_fcs_path = os.path.join(flowkit_path,'fcs_samples')
flowkit_wsp_path = os.path.join(flowkit_path,'wsp_files')
flowkit_visualize_path = os.path.join(flowkit_path,'plots')

In [ ]:


plot_dict_all = {}
for key in meta_info['clusterkeys']:
    cluster = meta_info['clusterkeys'][key]
    wsp_path = os.path.join(flowkit_wsp_path,'wsp_cluster_' + str(cluster) + '.wsp')
    fcs_path = os.path.join(flowkit_fcs_path,'fcs_cluster_' + str(cluster) + '.fcs')
    sample = fk.Sample(fcs_path,sample_id = cluster)
    wsp = fk.Workspace(wsp_path, sample)
    wsp.analyze_samples()
    plot_dict = {}
    for h_string in list(wsp.get_analysis_report()['gate_name'].values):
        p = wsp.plot_gate(
            cluster,
            h_string,
            subsample_count=10e8)
        plot_dict[h_string] = p
    plot_dict_all[cluster] = plot_dict 
if not os.path.exists(flowkit_visualize_path):
            os.mkdir(flowkit_visualize_path)
np.save(os.path.join(flowkit_visualize_path, "flowkit_plots.npy"), plot_dict_all)

In [80]:
save(plot_dict_all)

The following commands were written to file `(plot_dict_all).py`:
import numpy as np
import bokeh
from bokeh.plotting import show
import matplotlib.pyplot as plt
import flowkit as fk
import os
import pandas as pd
#import convexgating
bokeh.io.output_notebook()
get_ipython().run_line_magic('matplotlib', 'inline')

_ = plt.ioff()
def make_gate_edges_object_string(cluster,hierarchy):
    return 'cluster_' + cluster + '_gate_edges_hierarchy_' + str(hierarchy) + '.csv'

def get_flowkit_gating_strategy(base_path,cluster):
    #base_path: location of ConvexGating output files
    #cluster: cluster identifier in ConvexGating run

    # initialize flowkit gating strategy
    #key_cl = next((key for key, value in cg_meta_info['clusterkeys'].items() if value == cluster), None)
    #print(key_cl)
    g_strat = fk.GatingStrategy()

    # get gating depth
    perf_summary_df = pd.read_csv(os.path.join(base_path,'performance_summary.csv'))
    marker_csv = pd.read_csv(os.path.join(base_path,'marker_s

In [74]:
show(plot_dict_all['CD4+ T cell']['hierarchy_1'])

In [20]:
wsp_path = os.path.join(flowkit_wsp_path,'wsp_cluster_' + str(cluster) + '.wsp')
fcs_path = os.path.join(flowkit_fcs_path,'fcs_cluster_' + str(cluster) + '.fcs')

In [62]:
#wsp_path = 'test_' + str(cluster) + '.wsp'
sample = fk.Sample(fcs_path,sample_id = cluster)
wsp = fk.Workspace(wsp_path, sample)
wsp.analyze_samples()

In [65]:
plot_dict_all = {}
for
plot_dict = {}
for h_string in list(wsp.get_analysis_report()['gate_name'].values):
    p = wsp.plot_gate(
        cluster,
        h_string,
        subsample_count=10e8)
    #show(p)
    plot_dict[h_string] = p

In [68]:
show(plot_dict['hierarchy_1'])

In [37]:
wsp.analyze_samples()

In [48]:
p = wsp.plot_gate(
        cluster,
        'hierarchy_1',
        subsample_count=10e8)
show(p)

In [51]:
plot_dict = {}

In [52]:
plot_dict['test'] = p 

In [54]:
show(plot_dict['test'])

In [50]:
save(p)

The following commands were written to file `(p).py`:
import numpy as np
import bokeh
from bokeh.plotting import show
import matplotlib.pyplot as plt
import flowkit as fk
import os
import pandas as pd
#import convexgating
bokeh.io.output_notebook()
get_ipython().run_line_magic('matplotlib', 'inline')

_ = plt.ioff()
def make_gate_edges_object_string(cluster,hierarchy):
    return 'cluster_' + cluster + '_gate_edges_hierarchy_' + str(hierarchy) + '.csv'

def get_flowkit_gating_strategy(base_path,cluster):
    #base_path: location of ConvexGating output files
    #cluster: cluster identifier in ConvexGating run

    # initialize flowkit gating strategy
    #key_cl = next((key for key, value in cg_meta_info['clusterkeys'].items() if value == cluster), None)
    #print(key_cl)
    g_strat = fk.GatingStrategy()

    # get gating depth
    perf_summary_df = pd.read_csv(os.path.join(base_path,'performance_summary.csv'))
    marker_csv = pd.read_csv(os.path.join(base_path,'marker_summary.csv')